In [18]:
import datetime
import requests

from bs4 import BeautifulSoup
import pandas as pd

requests_session = requests.Session()

dates = []
topics = []
titles = []
contents = []  # Новый список для хранения текста статей

for day in range(0, 2):
    num_pages = 1
    while True:
        date = (datetime.datetime.today() - datetime.timedelta(days=day)).strftime('%Y/%m/%d')
        url = f'https://lenta.ru/{date}/page/{num_pages}/'
        link = requests_session.get(url)
        soup = BeautifulSoup(link.text, 'lxml')
        
        news_list = soup.find_all('a', {"class": "card-full-news _archive"}, href=True)
        if len(news_list) == 0:
            # Если на странице нет новостей, переходим к следующей дате
            break

        for news in news_list:
            # Дата
            dates.append(date)
            
            # Заголовок
            title = news.find_all('h3', {"class": "card-full-news__title"})
            titles.append(title[0].get_text() if len(title) > 0 else 'None')
            
            # Рубрика/тема
            topic = news.find_all('span', {"class": "card-full-news__info-item card-full-news__rubric"})
            topics.append(topic[0].get_text() if len(topic) > 0 else 'None')
            
            # Переходим по ссылке, чтобы собрать текст статьи
            news_url = 'https://lenta.ru' + news['href']
            article_req = requests_session.get(news_url)
            article_soup = BeautifulSoup(article_req.text, 'lxml')
            
            # Ищем все абзацы с классом topic-body__content-text
            paragraphs = article_soup.find_all('p', class_='topic-body__content-text')
            
            # Склеиваем все абзацы в одну строку
            news_content = ' '.join([p.get_text(strip=True) for p in paragraphs])
            contents.append(news_content)
        
        num_pages += 1

# Формируем DataFrame, добавляя столбец 'content'
df = pd.DataFrame({
    'dates': dates,
    'topics': topics,
    'titles': titles,
    'content': contents
})

df['dates'] = pd.to_datetime(df['dates'])


In [19]:
df

dates           topics  \
0   2025-03-12      Бывший СССР   
1   2025-03-12           Россия   
2   2025-03-12      Бывший СССР   
3   2025-03-12  Наука и техника   
4   2025-03-12              Мир   
..         ...              ...   
796 2025-03-11              Мир   
797 2025-03-11      Бывший СССР   
798 2025-03-11              Мир   
799 2025-03-11           Россия   
800 2025-03-11      Бывший СССР   

                                                titles  \
0    На Украине назвали условие для переговоров с Р...   
1    12 марта: какой праздник отмечают в России и мире   
2    На Украине заявили о возобновлении помощи со с...   
3              ВСУ заковали немецкую БМП Marder в цепи   
4    Макрон прокомментировал возможное прекращение ...   
..                                                 ...   
796   Раскрыта цель Трампа в урегулировании на Украине   
797  На Украине подвели итоги переговоров в Саудовс...   
798  Трамп допустил полное прекращение огня на Укра...   
799  В Госдуме прокомментировали готовность Украины...   
800  На Украине анонсировали переговоры с США о пре...   

                                               content  
0    Главаофиса президентаУкраиныВладимира Зеленско...  
1    В России 12 марта празднуют День запрета на ун...  
2    Замглавы офиса президента Украины Павел Палиса...  
3    БойцыВооруженных силУкраины(ВСУ) заковали неме...  
4    ПрезидентФранцииЭммануэль Макронзаявил, что пр...  
..                                                 ...  
796  Бывший британский дипломат и экс-сотрудник MI-...  
797  Бывший советникофиса президентаУкраиныАлексей ...  
798  ПрезидентСШАДональд Трампрассчитывает, что реж...  
799  ДепутатГосдумыМихаил Шереметв беседе сТАССпрок...  
800  Главаофиса президентаУкраиныВладимира Зеленско...  

[801 rows x 4 columns]

In [25]:
df_economy = df[(df['topics'] == 'Экономика') | (df['topics'] == 'Политика') | (df['topics'] == 'Интернет и СМИ')]
df_economy


dates          topics  \
16  2025-03-12       Экономика   
21  2025-03-12       Экономика   
26  2025-03-12  Интернет и СМИ   
53  2025-03-12       Экономика   
61  2025-03-12       Экономика   
..         ...             ...   
730 2025-03-11       Экономика   
757 2025-03-11       Экономика   
759 2025-03-11  Интернет и СМИ   
767 2025-03-11  Интернет и СМИ   
791 2025-03-11       Экономика   

                                                titles  \
16       Пенсию некоторых россиян предложили увеличить   
21   Мошенники начали использовать самозапрет на кр...   
26   Мужчина дал совет одному сыну и случайно разру...   
53   Синоптик допустил влияние потепления климата н...   
61   Власти разъяснили запрет на иностранные мессен...   
..                                                 ...   
730  В США оценили эффективность санкций против рос...   
757  Медиахолдинг МАЕР поддержит ветеранов СВО в ра...   
759  Живущая в доме престарелых телеведущая бросила...   
767       Названа угроза для переговоров США и Украины   
791  Россиянам рассказали про налоги за сараи и дач...   

                                               content  
16   ДепутатыГосдумыотЛДПРпредложили ввести доплату...  
21   Мошенники воспользовались недавно заработавшим...  
26   ПользовательRedditс ником Samus 10011 поделилс...  
53   Научный руководитель ГидрометцентраРоман Вильф...  
61   Сотрудникам банков введут запрет на использова...  
..                                                 ...  
730  Эффективность западных санкций в отношении рос...  
757  Медиахолдинг МАЕР заявил о готовности предоста...  
759  Известная американская телеведущая Венди Уилья...  
767  Присутствие руководителяофиса президентаУкраин...  
791  Информация о том, что в России ввели обязатель...  

[138 rows x 4 columns]

In [22]:
df['topics'].value_counts()

topics
Россия               174
Мир                  122
Экономика            100
Бывший СССР           86
Силовые структуры     71
Наука и техника       41
Путешествия           39
Интернет и СМИ        38
Ценности              29
Культура              28
Из жизни              27
Забота о себе         22
Спорт                 22
69-я параллель         2
Name: count, dtype: int64

In [26]:
all_news = df['content'].values
all_news


array(['Главаофиса президентаУкраиныВладимира ЗеленскогоАндрей Ермакпрокомментировал предложениеСШАо прекращении огня на 30 дней. Его слова приводитРИА Новости. Ермак назвал условие для переговоров с Россией и подчеркнул, что дляКиеваважно согласиеМосквына прекращение огня. «Разумеется, мы готовы безостановочно работать над подготовкой, вести переговоры о следующем этапе, потому что, разумеется, это только первый шаг», — отметил он. Ранее Украинавыразилаготовность принять предложение США по немедленному прекращению огня. Соединенные Штаты отменяют паузу в обмене разведданными и восстанавливают помощь в обеспечении безопасности Украины. 27 февраля президент РоссииВладимир Путинзаявил, что Москва никогда не отказывалась решать украинский кризис мирным способом. При этом российская сторона настаивает на урегулировании конфликта путем устранения причин его возникновения и достижения такого соглашения, которое окончательно положило бы конец боевым действиям.',
       'В России 12 марта праз

In [27]:
prompt = """
Ты — бизнес-аналитический агент, твоя задача:

Внимательно прочитать предоставленные большие списки новостей, относящихся к России, из различных источников.

Провести глубокий и комплексный анализ:

Выделить ключевые события и тренды.

Кратко сформулировать основные новости дня.

Определить наиболее важные бизнес-проблемы, выявленные в результате анализа новостей:

Каждая проблема должна быть ясно сформулирована, с указанием причины или контекста её возникновения.

Для каждой выявленной проблемы предложить чёткое и практическое бизнес-решение, опираясь на лучшие практики бизнеса, успешные кейсы или проверенные стратегии:

Указывать конкретные шаги, которые помогут компании или предпринимателю извлечь выгоду и заработать на выявленной проблеме или минимизировать убытки.

Формат твоего ответа должен быть следующим:

Краткая сводка новостей:

(Коротко перечислить самые значимые события и тренды дня.)

Выявленные бизнес-проблемы и решения:

Проблема №1: (Описание проблемы)

Решение: (Предложение конкретного, практического решения проблемы)

Проблема №2: (Описание проблемы)

Решение: (Предложение конкретного, практического решения проблемы)

(И так далее по каждой проблеме.)

Примеры формулировок проблем и решений:

Проблема: Компания теряет рыночную долю из-за появления более дешёвых конкурирующих продуктов.

Решение: Рассмотреть стратегию снижения себестоимости производства или разработку нишевого продукта с уникальными характеристиками.

Проблема: Авария на танкере вызвала экологический кризис, влияющий на туристическую привлекательность региона.

Решение: Оперативно перенаправить туристические потоки в другие регионы, минимизируя убытки и предлагая клиентам выгодные альтернативы.

Проблема: Правительство Сирии снизило экспортные пошлины на сырьевые товары.

Решение: Немедленно наладить каналы импорта этих товаров с целью перепродажи на внутреннем рынке, воспользовавшись ценовым преимуществом.

Всегда помни, что твоя цель — помогать зарабатывать на выявленных проблемах.
"""


In [29]:
from openai import OpenAI

# Преобразуем numpy-массив в строку
system_text = str(prompt)        # или " ".join(prompt) если prompt – массив строк
user_text = str(all_news)         # аналогично для all_news

client = OpenAI(
  base_url="https://openrouter.ai/api/v1",
  api_key="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",
)

completion = client.chat.completions.create(
  extra_body={},
  model="google/gemini-2.0-pro-exp-02-05:free",
  messages=[
    {
      "role": "system",
      "content": [
        {
          "type": "text",
          "text": system_text
        }
      ]
    },
    {
      "role": "user",
      "content": [
        {
          "type": "text",
          "text": user_text
        }
      ]
    }
  ]
)
print(completion.choices[0].message.content)

## Краткая сводка новостей:

**Ключевые события и тренды, касающиеся России, за 11-12 марта 2025 года:**

*   **Украинский конфликт:** Украина согласилась на предложенное США 30-дневное прекращение огня, США возобновили военную помощь и обмен разведданными с Украиной. Ожидаются дальнейшие переговоры, в том числе с участием России. Российские войска продолжают наступление в Курской области, освобождая населенные пункты. ВСУ атаковали российские регионы с помощью большого количества беспилотников, есть погибшие и раненые среди гражданского населения.
*   **Внутренняя политика и экономика:** Предлагается ввести доплаты к пенсии, кредитную амнистию и контроль над ценами. Банкам могут запретить использование иностранных мессенджеров для делового общения с клиентами. Зафиксировано падение поставок умных часов. Обсуждается возможное смягчение антироссийских санкций.
*   **Международные отношения:** Турция готова выступить посредником в урегулировании украинского конфликта. США "отдадут" Украи

In [ ]:
# -*- encoding: utf-8 -*-
import urllib.request
import re
import sys

"""
ОПИСАНИЕ
скрипт парсит страницы LENTA.ru сы ссылками вида "https://lenta.ru/articles/..." и "https://lenta.ru/news/..."
для того чтобы определить еще какие либо страницы, можно составить регулярное выражение, 
и вставить проверку параметра self.article на пустоту, если он будет пустой, тогда можно 
регуляркой вытащить другой тег, не только article и обрабатывать его содержимое

После получения и очистки контент сохраняется в файл с именем страницы (если сылка вида 
https://lenta.ru/articles/2016/05/20/loan - то контент сохраняется в файл loan.txt рядом
со скриптом) 

Внизу указаны проверочные страницы
"""

class ParseMyClass:
	def __init__(self,url):
		self.url=url
		self.file = self.url.split('/')[-1]
		site = urllib.request.urlopen(self.url)
		html = str(site.read().decode('utf-8'))
		self.article = re.findall(r'<article[^>]*>(.*?)</article>', str(html), re.DOTALL)
		if len(self.article)==0:
			self.article = re.findall(r'<div.*itemtype="http://schema.org/NewsArticle[^>]+?>(.*)</div>', str(html) , re.DOTALL)
		self.razbor()
		self.save()
		
	def razbor(self):
		article = self.article

		#меняем ссылки
		article = re.sub(r'<[aA]\s{1}href=[\'\"](.*?)[\'\"][^>]*>(.*?)</[aA]>', r'[URL="\1"] \2 [/URL]', str(article))

#		#Тут надо будет подумать, как получше это сделать		
#		#выбираем фотки
#		article = re.sub(r'<img(.*?)alt=[\'\"](.*?)[\'\"](.*?)src=[\'\"](.*?)[\'\"](.*?)>', r'[IMG="\4"]\2[/IMG]', str(article))
		
		#удаляем различные теги для чистоты
		article = re.sub(r'<(section|script|aside|time).*?</\1>(?s)', '', str(article))
		article = re.sub(r'<div class="bordered-title">(.*)</div>', '', str(article))
		
		#удаляем лишние пробелы
		article = re.sub(r'\s+',' ', str(article))
		
		#удаляем табуляцию
		article = re.sub(r'\t', r'\s', str(article))
		
		#выделяем заголовки
		article = re.sub(r'<[hH][^>]*>(.*?)</[hH][^>]*>', r'\1\r\n', str(article))
		
		# выделяем абзацы
		article = re.sub(r'<[pP][^>]*>(.*?)</[pP][^>]*>', r'\1\r\n', str(article))
		
		# удаляем все оставльные теги
		article = re.sub(r'<.*?>','', str(article))
		
		# Выравниваем по 80 символов
		article.strip()
		list = article.split('\r\n')
		i=0
		j=79
		while i<len(list):
			if len(list[i])>j:
				shag=1
				k=j*shag
				nachalo_stroki=0
				while 0<k<=len(list[i]):
					if ord(list[i][k])!=32:
						while  list[i][k] is not None and list[i][k]!=' ' and list[i][k]!='\n' and k>nachalo_stroki:
							k=k-1
					if k==nachalo_stroki:
						list[i]=list[i][:j+nachalo_stroki]+'\n'+list[i][j+nachalo_stroki:]
					else:
						list[i]=list[i][:k]+'\n'+list[i][k+1:]
					k=(j*shag)-k
					shag=shag+1
					k=(j*shag)-k
					nachalo_stroki=k-j
			i=i+1
		article = str('\r\n'.join(list))
		self.article = article
		
	def save(self):
		fname=self.file+'.txt'
		f = open(fname, 'w')
		f.write(str(self.article))
		f.close()

if len (sys.argv) > 1:
	parse = ParseMyClass(sys.argv[1])
else:
	url = input('Введите URL статьи в виде "https://lenta.ru/articles/..."')
	if url is not None and len(url.strip())>0:
		parse = ParseMyClass(url)
		
#parse = ParseMyClass('https://lenta.ru/articles/2016/05/20/loan')		
#parse = ParseMyClass('https://lenta.ru/articles/2016/05/20/nogotkov')	
#parse = ParseMyClass('https://lenta.ru/articles/2016/05/20/platinum')	
#parse = ParseMyClass('https://lenta.ru/articles/2016/05/21/dnepr')	
#parse = ParseMyClass('https://lenta.ru/articles/2016/05/21/scaryipoteka/')	
#parse = ParseMyClass('https://lenta.ru/articles/2016/05/18/minigun')
#parse = ParseMyClass('https://lenta.ru/news/2016/05/21/fireinthesky')
#parse = ParseMyClass('https://lenta.ru/news/2016/05/21/ducks')

In [ ]:
# БЕЗ КОНТЕНТА - ТЕКСТА НОВОСТИ

import datetime
import requests

from bs4 import BeautifulSoup
import pandas as pd

requests_session = requests.Session()

dates = []
topics = []
titles = []

for day in range(0,2):
  num_pages = 1
  while True: #получить все новости за дату разом нельзя, как и узнать количество страниц, поэтому пришлось прибегнуть к while:
    date = ((datetime.datetime.today() - datetime.timedelta(days=day)).strftime('%Y/%m/%d'))
    link = requests_session.get('https://lenta.ru/{}/page/{}/'.format(date, num_pages))  
    soup = BeautifulSoup(link.text, 'lxml')
    news_list = soup.find_all('a', {"class": "card-full-news _archive"}, href=True)
    if len(news_list) == 0: #если на странице нет новостей, переходим к следующей дате
      break
            
    for news in news_list: #собираем данные по каждой новости
      dates.append(date)
      title = news.find_all('h3', {"class": "card-full-news__title"})
      titles.append((title[0].get_text() if len(title) > 0 else 'None'))
      topic = news.find_all('span', {"class": "card-full-news__info-item card-full-news__rubric"})
      topics.append((topic[0].get_text() if len(topic) > 0 else 'None'))
    num_pages+=1
                
df = pd.DataFrame({'dates': dates, 'topics': topics, 'titles': titles })
df['dates'] = pd.to_datetime(df['dates'])
